# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [RecurrentPPO]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 517, done.
remote: Counting objects: 100% (124/124), done.
remote: Compressing objects: 100% (59/59), done.
remote: Total 517 (delta 65), reused 121 (delta 64), pack-reused 393
Receiving objects: 100% (517/517), 188.99 MiB | 15.60 MiB/s, done.
Resolving deltas: 100% (214/214), done.
Checking out files: 100% (223/223), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          RL_VPP_Thesis/
Algorithm_simulator_notebooks/    trained_models/
data/                             VPP_environment.py
EV_experiment_notebooks/          VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  wandb/
README.md


In [3]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')
wandb, version 0.13.4


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f11d03144d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
#env.plot_VPP_input_data()

Charging event: 1, Arrival time: 2022-01-01 05:45:00, Parking_time: 24, Leaving_time: 2022-01-02 05:45:00, SOC: 0.614788016851822, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1043, Arrival time: 2022-12-31 17:00:00, Parking_time: 24, Leaving_time: 2023-01-01 17:00:00, SOC: 0.5144773147005901, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en=kWh  4947.18 , RE-to-vehicle_unused_en=kWh  -26161.81 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21203.11 , Grid_used_en=kWh  38590.79 , RE-to-vehicle_unused_en=kWh  17387.69 , Total_selling_cost=€  872.59 , Grid_cost=€  1371.93 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08


In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21722.38 , Grid_used_en=kWh  39200.04 , RE-to-vehicle_unused_en=kWh  17477.66 , Total_selling_cost=€  847.26 , Grid_cost=€  1369.93 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


In [9]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb"


In [10]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

model_id = "s37o8q0n"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [11]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21913.59 , Grid_used_en=kWh  39215.6 , RE-to-vehicle_unused_en=kWh  17302.02 , Total_selling_cost=€  903.99 , Grid_cost=€  1401.51 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3793.42 , Grid_used_en=KWh  2035.55 , RE-to-vehicle_unused_en=KWh  5828.97 , Total_selling_cost=€  -73.1 , Grid_cost=€  72.54 
 EV_INFO: Av.EV_energy_leaving=kWh  66.77 , Std.EV_energy_leaving=kWh  26.54 , EV_departures =  1038 , EV_queue_left =  1
SCORE:  Cumulative_reward= 383539.91 - Step_rewars (load_t= 354068.42, EVs_energy_t= 6427.96)
 - Final_rewards (Av.EVs_energy= 16747.22, Grid_used_en= -1302.31, RE-to-vehicle_unused_en= -2566.79, Grid_cost= 10165.4)
Episode:1 Score:383539.9060544787


In [12]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  66.759201  79.449791  27.115017  97.329155   
2022-06-06 05:00:00  67.867378  80.557968  26.865017  98.437332   
2022-06-06 05:15:00  68.949364  81.639954  26.615017  99.519318   
2022-06-06 05:30:00  70.048325  82.738914  26.365017  99.989998   
2022-06-06 05:45:00  71.164612  83.855202  26.115017  99.989998   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 2, 2, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [2528, 2527, 2529, 2526]  [1, 1, 2, 1]   
2022-06-06 05:00:00  [2528, 2527, 2529, 2526]  [1, 1, 2, 1]   
2022-06-06 05:15:00  [2528, 2527, 2529, 2526]  [1, 1, 2, 1]   
2022-06-06 05:30:00  [2528, 2527, 2529, 2526]  [1, 1, 2, 1]   
2022-06-06 05:45:00  [2528, 2527, 2529, 2526]  [1, 1, 2, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00  [False, False, False, False]        0.000000   
2022-01-01 00:30:00  [False, False, False, False]        0.000000   
2022-01-01 00:45:00  [False, False, False, False]        0.000000   
2022-01-01 01:00:00  [False, False, False, False]        0.000000   
...                                           ...             ...   
2022-06-06 04:45:00    [True, True, False, False]        8.697046   
2022-06-06 05:00:00    [True, True, False, False]       13.298083   
2022-06-06 05:15:00    [True, True, False, False]       12.983812   
2022-06-06 05:30:00    [True, True, False, False]       10.674399   
2022-06-06 05:45:00    [True, True, False, False]        8.930331   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0  1.779130e+00    -4.098943        0.0   
2022-01-01 00:15:00                0.0  2.959366e+00    -4.708773        0.0   
2022-01-01 00:30:00                0.0  3.325264e+00    -0.897480        0.0   
2022-01-01 00:45:00                0.0  1.038488e+00    -2.296167        0.0   
2022-01-01 01:00:00                0.0  1.877700e+00    11.774528        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:00:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:15:00               -1.0 -1.776357e-15    -2.521842        0.0   
2022-06-06 05:30:00               -1.0 -2.513105e+00    -5.422866        0.0   
2022-06-06 05:45:00               -1.0 -4.465153e+00    -5.410880        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.098943  
2022-01-01 00:15:00  -4.708773  
2022-01-01 00:30:00  -0.897480  
2022-01-01 00:45:00  -2.296167  
2022-01-01 01:00:00  11.774528  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  -2.521842  
2022-06-06 05:30:00  -5.422866  
20

In [14]:
#env.plot_Elvis_results()

In [15]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [16]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [17]:
env.plot_VPP_Elvis_comparison()

In [18]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [19]:
env.plot_rewards_stats()

In [20]:
env.plot_EVs_kpi()

In [21]:
env.plot_load_kpi()

In [22]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [23]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 3130, Arrival time: 2022-01-01 09:45:00, Parking_time: 24, Leaving_time: 2022-01-02 09:45:00, SOC: 0.6322069635923269, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 4172, Arrival time: 2022-12-31 16:15:00, Parking_time: 21.94750720361445, Leaving_time: 2023-01-01 14:11:51.025933, SOC: 0.5783397834970736, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en=kWh  2136.67 , RE-to-vehicle_unused_en=kWh  -32222.06 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  11719.59 , Grid_used_en=kWh  33895.78 , RE-to-vehicle_unused_en=kWh  22176.2 , Total_selling_cost=€  569.97 , Grid_cost=€  1481.18 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [24]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
#plot_VPP_input_data.show()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12378.98 , Grid_used_en=kWh  34793.04 , RE-to-vehicle_unused_en=kWh  22414.06 , Total_selling_cost=€  629.56 , Grid_cost=€  1538.32 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....


In [25]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [26]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12868.55 , Grid_used_en=kWh  34773.49 , RE-to-vehicle_unused_en=kWh  21904.94 , Total_selling_cost=€  611.15 , Grid_cost=€  1510.25 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7242.13 , Grid_used_en=KWh  996.31 , RE-to-vehicle_unused_en=KWh  8238.44 , Total_selling_cost=€  -273.44 , Grid_cost=€  43.06 
 EV_INFO: Av.EV_energy_leaving=kWh  71.58 , Std.EV_energy_leaving=kWh  25.7 , EV_departures =  1038 , EV_queue_left =  1
SCORE:  Cumulative_reward= 396772.13 - Step_rewars (load_t= 346689.38, EVs_energy_t= 21212.98)
 - Final_rewards (Av.EVs_energy= 17942.55, Grid_used_en= -353.12, RE-to-vehicle_unused_en= -3301.87, Grid_cost= 14582.21)
Episode:1 Score:396772.12609804503


In [27]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
VPP_table.head(15000)

0    1          2    3           EVs_id       actions  \
time                                                                           
2022-01-01 00:00:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [1, 1, 1, 1]   
2022-01-01 00:15:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [1, 1, 1, 1]   
2022-01-01 00:30:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 1, 1, 0]   
2022-01-01 00:45:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 1, 1, 0]   
2022-01-01 01:00:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 1, 1, 0]   
...                  ...  ...        ...  ...              ...           ...   
2022-06-06 04:45:00  0.0  0.0  93.280418  0.0  [0, 0, 5631, 0]  [0, 0, 1, 0]   
2022-06-06 05:00:00  0.0  0.0  96.030418  0.0  [0, 0, 5631, 0]  [0, 0, 1, 0]   
2022-06-06 05:15:00  0.0  0.0  98.780418  0.0  [0, 0, 5631, 0]  [0, 0, 1, 0]   
2022-06-06 05:30:00  0.0  0.0  99.989998  0.0  [0, 0, 5631, 0]  [0, 0, 1, 0]   
2022-06-06 05:45:00  0.0  0.0  99.989998  0.0  [0, 0, 5631, 0]  [0, 0, 1, 0]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00  [False, False, False, False]        0.000000   
2022-01-01 00:30:00    [True, False, False, True]        0.000000   
2022-01-01 00:45:00    [True, False, False, True]        0.000000   
2022-01-01 01:00:00    [True, False, False, True]        0.000000   
...                                           ...             ...   
2022-06-06 04:45:00      [True, True, True, True]       11.000000   
2022-06-06 05:00:00      [True, True, True, True]       11.000000   
2022-06-06 05:15:00      [True, True, True, True]       11.000000   
2022-06-06 05:30:00      [True, True, True, True]        4.838326   
2022-06-06 05:45:00      [True, True, True, True]        0.000009   

                     ev_discharged_pwr       load  load_reward  EV_reward  \
time                                                                        
2022-01-01 00:00:00                0.0  -3.182123    -5.537917        0.0   
2022-01-01 00:15:00                0.0  -4.591709    -4.773844        0.0   
2022-01-01 00:30:00                0.0  -3.864306    -4.489387        0.0   
2022-01-01 00:45:00                0.0  -3.693632    -5.598558        0.0   
2022-01-01 01:00:00                0.0  -4.658414    -5.866933        0.0   
...                                ...        ...          ...        ...   
2022-06-06 04:45:00                0.0  -0.855742    -2.923048        0.0   
2022-06-06 05:00:00                0.0  -2.753829    -4.311366        0.0   
2022-06-06 05:15:00                0.0  -3.586820    -9.203868        0.0   
2022-06-06 05:30:00                0.0  -8.624255   -13.908899        0.0   
2022-06-06 05:45:00                0.0 -13.799789   -15.789646        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.537917  
2022-01-01 00:15:00  -4.773844  
2022-01-01 00:30:00  -4.489387  
2022-01-01 00:45:00  -5.598558  
2022-01-01 01:00:00  -5.866933  
...                        ...  
2022-06-06 04:45:00  -2.923048  
2022-06-06 05:00:00  -4.311366  
2022-06-06 05:15:00  -9.203868  
2022-06-06 05:30:00 -13.908899  
2022-06-06 05:45:00 -15.789646  

[15000 rows x 13 columns]

In [29]:
#env.plot_Elvis_results()

In [30]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [31]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [32]:
env.plot_VPP_Elvis_comparison()

In [33]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [34]:
env.plot_rewards_stats()

In [35]:
env.plot_EVs_kpi()

In [36]:
env.plot_load_kpi()

In [37]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [38]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 6259, Arrival time: 2022-01-01 07:00:00, Parking_time: 23.466770622462235, Leaving_time: 2022-01-02 06:28:00.374241, SOC: 0.5596173349379839, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 7301, Arrival time: 2022-12-31 19:30:00, Parking_time: 24, Leaving_time: 2023-01-01 19:30:00, SOC: 0.6063574733139007, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en=kWh  1556.25 , RE-to-vehicle_unused_en=kWh  -35673.95 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8636.44 , Grid_used_en=kWh  32129.47 , RE-to-vehicle_unused_en=kWh  23493.03 , Total_selling_cost=€  458.26 , Grid_cost=€  1336.94 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [39]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
#plot_VPP_input_data.show()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8809.22 , Grid_used_en=kWh  32165.0 , RE-to-vehicle_unused_en=kWh  23355.78 , Total_selling_cost=€  500.09 , Grid_cost=€  1352.86 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....


In [40]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [41]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8450.45 , Grid_used_en=kWh  31952.22 , RE-to-vehicle_unused_en=kWh  23501.76 , Total_selling_cost=€  482.46 , Grid_cost=€  1348.22 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -8652.86 , Grid_used_en=KWh  794.37 , RE-to-vehicle_unused_en=KWh  9447.22 , Total_selling_cost=€  -291.42 , Grid_cost=€  33.5 
 EV_INFO: Av.EV_energy_leaving=kWh  74.47 , Std.EV_energy_leaving=kWh  24.59 , EV_departures =  1041 , EV_queue_left =  0
SCORE:  Cumulative_reward= 391583.42 - Step_rewars (load_t= 330779.23, EVs_energy_t= 30892.09)
 - Final_rewards (Av.EVs_energy= 18618.63, Grid_used_en= -198.41, RE-to-vehicle_unused_en= -3787.11, Grid_cost= 15278.99)
Episode:1 Score:391583.41835895303


In [42]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [43]:
VPP_table.head(14995)

0          1    2          3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000  0.0   0.000000   
2022-01-01 00:15:00   0.000000   0.000000  0.0   0.000000   
2022-01-01 00:30:00   0.000000   0.000000  0.0   0.000000   
2022-01-01 00:45:00   0.000000   0.000000  0.0   0.000000   
2022-01-01 01:00:00   0.000000   0.000000  0.0   0.000000   
...                        ...        ...  ...        ...   
2022-06-06 03:30:00  73.072510  48.258163  0.0  82.675957   
2022-06-06 03:45:00  73.693192  48.008163  0.0  83.296638   
2022-06-06 04:00:00  74.631004  47.758163  0.0  84.234451   
2022-06-06 04:15:00  75.495514  47.508163  0.0  85.098961   
2022-06-06 04:30:00  76.611183  47.258163  0.0  86.214630   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [1, 1, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [1, 1, 0, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [0, 1, 0, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [0, 1, 0, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [0, 1, 1, 0]   
...                                    ...           ...   
2022-06-06 03:30:00  [8788, 8789, 0, 8787]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [8788, 8789, 0, 8787]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [8788, 8789, 0, 8787]  [1, 2, 2, 1]   
2022-06-06 04:15:00  [8788, 8789, 0, 8787]  [1, 2, 2, 1]   
2022-06-06 04:30:00  [8788, 8789, 0, 8787]  [1, 2, 2, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00   [False, False, True, True]        0.000000   
2022-01-01 00:30:00    [True, False, True, True]        0.000000   
2022-01-01 00:45:00    [True, False, True, True]        0.000000   
2022-01-01 01:00:00   [True, False, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [True, False, False, True]        4.572750   
2022-06-06 03:45:00   [True, False, False, True]        4.965448   
2022-06-06 04:00:00   [True, False, False, True]        7.502523   
2022-06-06 04:15:00   [True, False, False, True]        6.916049   
2022-06-06 04:30:00   [True, False, False, True]        8.925358   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.952847e+00    -3.558989        0.0   
2022-01-01 00:15:00                0.0 -3.135393e+00    -4.237418        0.0   
2022-01-01 00:30:00                0.0 -3.542451e+00    -3.797991        0.0   
2022-01-01 00:45:00                0.0 -3.278794e+00    -6.429280        0.0   
2022-01-01 01:00:00                0.0 -5.572208e+00    -7.218648        0.0   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 03:45:00               -1.0  4.440892e-16    15.000000        0.0   
2022-06-06 04:00:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:15:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:30:00               -1.0  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.558989  
2022-01-01 00:15:00  -4.237418  
2022-01-01 00:30:00  -3.797991  
2022-01-01 00:45:00  -6.429280  
2022-01-01 01:00:00  -7.218648  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.000000  
2022-06-06 04:15:00  15.000000  
2022-06-06 04:30:00  15.000000  

[14995 rows x 13 columns]

In [44]:
#env.plot_Elvis_results()

In [45]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [46]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [47]:
env.plot_VPP_Elvis_comparison()

In [48]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [49]:
env.plot_rewards_stats()

In [50]:
env.plot_EVs_kpi()

In [51]:
env.plot_actions_kpi()

In [52]:
env.plot_load_kpi()

In [53]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [54]:
#env.close()